# Riemann scheme. 

Lets consider same setup as in [ex_3a](https://github.com/AST-Course/AST5110/blob/main/ex_3a.ipynb) Burgers’ equation, i.e.,

$$\frac{\partial u}{\partial t} + u \frac{\partial u}{\partial x} = 0   \tag{1}$$ 

for the domain $x \in (x_0, x_f)$ with $x_0 = −1.4$, $x_f = 2.0$ with initial condition:

$$u(x,t=0) = A\left[\tanh\left(\frac{x+x_c}{W}\right)-\tanh\left(\frac{x-x_c}{W}\right)\right]   \tag{2}$$

whereby $A = 0.02$ , $x_c = 0.70$, $W = 0.1$. Let the solution evolve until time $t_f = 100$. However, let's now implement a new time-step method. Find the conservative form of the equation and implement a Rieman solver [wiki:Rieman Solvers](https://github.com/AST-Course/AST5110/wiki/Riemann-solvers). 

Add this to your library and solve the previous simulation imposing the CFL condition. For this exercise, fill in `nm_lib` the function `evolv_Rie_uadv_burgers`. 

In order to write Eq.1 on a conservative form, we recognize that we can write the second term as

$$
    \frac{\partial (u^2/2)}{\partial x} = \frac{1}{2}\cdot2u\frac{\partial u}{\partial x} = u\frac{\partial u}{\partial x}.
$$

We therefore denote the Flux $F$ as $u^2 /2$. 


In [1]:
import numpy as np 
import matplotlib.pyplot as plt 
from nm_lib import nm_lib as nm
from matplotlib.animation import FuncAnimation
from IPython.display import HTML

In [2]:
def initial_u(xx):
    r"""
    Returns initial condition of u(x,t) from Eq.2
    
    Requires
    ----------
    Numpy

    Parameters
    ----------
    x : `array`
        spatial array. 

    Returns
    ------- 
    u(x,t=0) : `array`
            Initial condition of u(x,t)
        
    """
    A = 0.02
    x_c = 0.7
    W = 0.1

    return A*(np.tanh((xx+x_c)/W) - np.tanh((xx-x_c)/W))

In [3]:
nint = 128
nump = nint +1 

x0 = -1.4
xf = 2.0

nt = 100

x = np.linspace(x0,xf, nump)
u0 = initial_u(x)

#### 1 step

Compute left and right of $u$, i.e., $u_L$ and $u_R$

#### 2 step
Compute from those the flux, i.e., $F_L$ and $F_R$

#### 3 step
Compute the propagating speed ($v_a[i]=max(|u[i],|u[i-1]|)$)

#### 4 step
Compute the interface fluxes (Rusanov)

$rhs=(F_R+F_L)/2 - v_a (U_R -U_L)$

#### 5 step
Advance in time $u^{n+1}=u^n + dt\times rhs$. What is dt? 


In [4]:
nt = 1000
t, un = nm.evolv_Rie_uadv_burgers(x, u0, nump, nt, bnd_limits=[1,1])

t_lax, un_lax = nm.evolv_Lax_uadv_burgers(x, u0, nt, ddx = nm.deriv_cent, bnd_limits=[1,1])

In [5]:
same = t_lax.reshape(len(t_lax),1) - t
same2 = np.where(np.abs(same)<0.05)

N = 10

In [6]:
plt.ioff()

fig, axes = plt.subplots(nrows=1, ncols=1, figsize=(10, 5))

def init(): 
    axes.plot(x,un[:,0])

def animate(i):
 
    axes.clear()
    axes.plot(x,un[:,::N][:,i])
    axes.set_title('t=%.2f'%t[::N][i])
    axes.set_xlabel(r"x")
    axes.set_ylabel(r"$u_i$")
    axes.grid()
    
anim = FuncAnimation(fig, animate, interval=50, frames=len(t[::N]), init_func=init)
HTML(anim.to_jshtml())


In [7]:
plt.close()

In [8]:
plt.ioff()

fig, axes = plt.subplots(nrows=1, ncols=1, figsize=(10, 5))

def init(): 
    axes.plot(x,un[:,0])
    axes.plot(x,un_lax[:,0])

def animate(i):
 
    axes.clear()
    axes.plot(x,un[:,same2[1]][:,::N][:,i], label="Riemann")
    axes.plot(x,un_lax[:,same2[0]][:,::N][:,i], label="LAX")
    axes.set_title('t=%.2f'%t[same2[1]][::N][i])
    axes.legend()
    axes.set_xlabel(r"x")
    axes.set_ylabel(r"$u_i$")
    axes.grid()
    
anim = FuncAnimation(fig, animate, interval=50, frames=len(t[same2[1]][::N]), init_func=init)
HTML(anim.to_jshtml())

In [9]:
plt.close()

Is this method less or more diffusive than Lax method? Find the analytical solution and compare. Where and when is better or worse than the Lax method? 

Since we use `dt = 0.98*np.min(dx/np.abs(va))` to compute the dt, it is depended on $v_a$ from the ($1/v_a$) term. 

From the animation above, we can see that the Riemann scheme is less diffusive than the Lax method. This is more visible at the shock on the right side, as the LAX method needs more steps to define the solution.

---
## TVD scheme. 

Combine the Lax method with the Rieman solver using a flux limiter scheme. For this, one needs to identify how large are the gradients. Lets define: 

$$r^{+}_i = \frac{u_i-u_{i-1}}{u_{i+1}+u_i}$$

What kind of properties do you see on $r^{+}_i$? e.g., what happens when $r\ge0$? or $r\le0$? 

now lets consider the following flux limiter: 

$$\phi = max\left(0,min\left(\theta r,\frac{1+r}{2},\theta \right)\right),\, \theta =[1,2]$$

Finally, combine the Lax from previous excersice with the Riemann solver using the flux limiter as follows: 

$$u^{n+1}_i = u^n_i + dt (f^n_{i+1/2}-f^n_{i-1/2})$$

Where 

$$f^n_{i+1/2} = f^{Riemann}_{i+1/2} + \phi^n_i (f^{L}_{i+1/2}-f^{Riemann}_{i+1/2})$$



When becomes purely Rieman solver? And Lax? Which others methods you can find depending on what is $r$ of $\phi$. 